# DATA PROCESSING FOR SUB DATA

In [1]:
# Importation des packages

# Base
import importlib
import functions
importlib.reload(functions)
from functions import *

# Data Management
import pandas as pd
import numpy as np

# Imput
from sklearn.impute import KNNImputer

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


/Users/hugopuybareau/Documents/GitHub/QRT_DATA_CHALLENGE/env_qrt/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Importation des données

home_teams = pd.read_csv('../data/Sub_Data/sub_home_team_statistics_df.csv', index_col=0)
away_teams = pd.read_csv('../data/Sub_Data/sub_away_team_statistics_df.csv', index_col=0)

In [3]:
# Renommer les colonnes pour pouvoir les différencier une fois les deux DF aggrégés.

home_teams.columns = 'HOME_' + home_teams.columns
away_teams.columns = 'AWAY_' + away_teams.columns

# Faire la concaténation
sub_data_teams = pd.concat([home_teams,away_teams],join='inner',axis=1)

sub_data_teams.shape

(25368, 280)

In [4]:
# Traitement des valeurs manquantes pour les statistiques sur les équipes

# nan_colormap(sub_data_teams, 'Vérification présence de NaNs')
spot_columns(sub_data_teams, percent=10)

Column 'HOME_TEAM_INJURIES_5_last_match_sum' has 10.66% NaN values
Column 'HOME_TEAM_INJURIES_5_last_match_average' has 10.64% NaN values
Column 'HOME_TEAM_BALL_SAFE_5_last_match_std' has 11.40% NaN values
Column 'HOME_TEAM_INJURIES_5_last_match_std' has 14.33% NaN values
Column 'AWAY_TEAM_INJURIES_5_last_match_sum' has 10.61% NaN values
Column 'AWAY_TEAM_INJURIES_5_last_match_average' has 10.59% NaN values
Column 'AWAY_TEAM_BALL_SAFE_5_last_match_std' has 11.39% NaN values
Column 'AWAY_TEAM_INJURIES_5_last_match_std' has 14.49% NaN values


In [5]:
# Pour l'imputing, on utilise la même stratégie quand dans le data_processing_train
# sauf qu'on va remplacer les 20% par 10%. 

# Je remplis d'abord toutes les colonnes où on observe moins de 10% de NaNs.

for col in sub_data_teams.columns[sub_data_teams.isna().mean() < 0.2]:
    sub_data_teams.fillna({col: sub_data_teams[col].median()}, inplace=True)

spot_columns(sub_data_teams, percent=0)

In [6]:
# Maintenant je remplis le reste avec un KNN Imputer. 

# sub_data_teams = sub_data_teams.reset_index()

# imputer = KNNImputer(n_neighbors=5)
# sub_data_teams = pd.DataFrame(imputer.fit_transform(sub_data_teams), columns=sub_data_teams.columns)

# spot_columns(sub_data_teams, percent=0)

In [7]:
# sub_data_teams.head(15)

In [8]:
# Ajout des données 'joueurs' 

home_players = pd.read_csv('../data/Sub_Data/sub_home_player_statistics_df.csv')
away_players = pd.read_csv('../data/Sub_Data/sub_away_player_statistics_df.csv')

train_home_players = pd.read_csv('../data/Train_Data/home_players_df.csv')
train_away_players = pd.read_csv('../data/Train_Data/away_players_df.csv')

# Renommer les colonnes pour pouvoir les différencier une fois les deux DF aggrégés.

home_players.columns = 'HOME_' + home_players.columns
away_players.columns = 'AWAY_' + away_players.columns

home_players = replacing(home_players)
away_players = replacing(away_players)

# home_players.shape --> (504626, 304)
# away_players.shape --> (504626, 304)
# nan_colormap(home_players, 'color map pour les home players')

In [9]:
# Vérification colonnes supprimées dans les données d'entraînement

def find_missing_columns_bidirectional(df1: pd.DataFrame, df2: pd.DataFrame) -> dict:

    missing_in_df2 = [col for col in df1.columns if col not in df2.columns]
    missing_in_df1 = [col for col in df2.columns if col not in df1.columns]
    
    return {
        'missing_in_df2': missing_in_df2,
        'missing_in_df1': missing_in_df1
    }

missing_columns_home_1 = find_missing_columns_bidirectional(train_home_players, home_players)

# print("Colonnes présentes dans 1 mais manquantes dans 2 :", missing_columns['missing_in_df2'])
# print("Colonnes présentes dans 2 mais manquantes dans 1 :", missing_columns['missing_in_df1'])

home_players = home_players.drop(columns=missing_columns_home_1['missing_in_df1'])

missing_columns_home_2 = find_missing_columns_bidirectional(train_home_players, home_players)

print("Colonnes présentes dans 2 mais manquantes dans 1 :", missing_columns_home_2['missing_in_df1'])

Colonnes présentes dans 2 mais manquantes dans 1 : []


In [10]:
missing_columns_away_1 = find_missing_columns_bidirectional(train_away_players, away_players)

# print("Colonnes présentes dans 1 mais manquantes dans 2 :", missing_columns['missing_in_df2'])
# print("Colonnes présentes dans 2 mais manquantes dans 1 :", missing_columns['missing_in_df1'])

away_players = away_players.drop(columns=missing_columns_away_1['missing_in_df1'])

missing_columns_away_2 = find_missing_columns_bidirectional(train_away_players, away_players)

print("Colonnes présentes dans 2 mais manquantes dans 1 :", missing_columns_away_2['missing_in_df1'])

Colonnes présentes dans 2 mais manquantes dans 1 : []


In [11]:
# Pour le traitement des NaNs dans ces tables, on fait la même chose que pour les équipes.
# On pense quand même à enlever les colonnes qui ont été supprimées dans le traitement des données
# d'entraînement. 

In [12]:
# Je remplis ensuite toutes les colonnes où on observe moins de 20% de NaNs.

home_players = home_players.fillna({'HOME_POSITION': home_players['HOME_POSITION'].mode()[0]})

for col in home_players.columns[home_players.isna().mean() < 0.5]:
    if home_players[col].dtype in ['float64', 'int64']:
        home_players.fillna({col: home_players[col].median()}, inplace=True)


spot_columns(home_players, percent=0)

In [13]:
# Je remplis ensuite toutes les colonnes où on observe moins de 20% de NaNs.

away_players = away_players.fillna({'AWAY_POSITION': away_players['AWAY_POSITION'].mode()[0]})

for col in away_players.columns[away_players.isna().mean() < 0.5]:
    if away_players[col].dtype in ['float64', 'int64']:
        away_players.fillna({col: away_players[col].median()}, inplace=True)

spot_columns(away_players, percent=0)


In [14]:
# Maintenant je remplis le reste avec un KNN Imputer. 

# imputer_home = KNNImputer(n_neighbors=3)
# home_players_imputed = pd.DataFrame(
#     imputer_home.fit_transform(home_players.drop(columns=['HOME_POSITION'], axis=1)),
#     columns=home_players.columns.drop('HOME_POSITION')
# )

# home_players = pd.concat([home_players['HOME_POSITION'], home_players_imputed], axis=1)

# home_players.head(5)

In [15]:
# imputer_away = KNNImputer(n_neighbors=3)
# away_players_imputed = pd.DataFrame(
#     imputer_away.fit_transform(away_players.drop(columns=['AWAY_POSITION'], axis=1)),
#     columns=away_players.columns.drop('AWAY_POSITION')
# )

# away_players = pd.concat([away_players['AWAY_POSITION'], away_players_imputed], axis=1)

# away_players.head(5)

In [16]:
# Je remets les colonnes dans le bonne ordre même si ce n'est pas obligatoire.

# cols = list(home_players.columns)
# col1_idx, col2_idx = cols.index('HOME_POSITION'), cols.index('HOME_ID')
# cols[col1_idx], cols[col2_idx] = cols[col2_idx], cols[col1_idx]
# home_players = home_players[cols]

# cols = list(away_players.columns)
# col1_idx, col2_idx = cols.index('AWAY_POSITION'), cols.index('AWAY_ID')
# cols[col1_idx], cols[col2_idx] = cols[col2_idx], cols[col1_idx]
# away_players = away_players[cols]

In [17]:
# Je vais agréger les colonnes par poste et par matchs pour réduire la taile du dataframe des joueurs.
# Il est important de le faire avant la fusion pour garder un lien entre les joueurs et les équipes comme 
# TEAM_NAME n'est pas dans le dataframe de soumission. 

columns_to_aggregate_home = [col for col in home_players.columns if col.endswith(('sum'))]
columns_to_aggregate_away = [col for col in away_players.columns if col.endswith(('sum'))]

# len(columns_to_aggregate_home)
# On garde 98+2 colonnes.

In [18]:
# Création des tables home_agg et away_agg pour les agréger avec la table sub_data_teams.

home_agg = home_players.groupby(['HOME_ID', 'HOME_POSITION']).agg({
    col: ['mean', 'max', 'min'] for col in columns_to_aggregate_home  # Agréger par la moyenne
}).reset_index()

away_agg = away_players.groupby(['AWAY_ID', 'AWAY_POSITION']).agg({
    col: ['mean', 'max', 'min'] for col in columns_to_aggregate_away  # Agréger par la moyenne également
}).reset_index()

home_agg.head(5)
# away_agg.head(5)

HOME_ID HOME_POSITION HOME_PLAYER_ACCURATE_CROSSES_season_sum             \
                                                           mean   max  min   
0   12303      attacker                                2.500000   7.0  0.0   
1   12303      defender                               14.500000  48.0  0.0   
2   12303    goalkeeper                                0.000000   0.0  0.0   
3   12303    midfielder                                8.909091  68.0  0.0   
4   12304      attacker                                5.666667  11.0  2.0   

  HOME_PLAYER_ACCURATE_PASSES_season_sum             \
                                    mean   max  min   
0                              11.250000  17.0  1.0   
1                              35.000000  70.0  0.0   
2                              13.000000  22.0  4.0   
3                              16.545455  39.0  0.0   
4                              13.333333  19.0  6.0   

  HOME_PLAYER_AERIALS_WON_season_sum              \
                                mean   max   min   
0                           1.750000   7.0   0.0   
1                          16.000000  31.0   0.0   
2                           1.000000   1.0   1.0   
3                           7.363636  31.0   0.0   
4                          21.666667  31.0  12.0   

  HOME_PLAYER_ASSISTS_season_sum              \
                            mean    max  min   
0                       5.000000   20.0  0.0   
1                       6.666667   20.0  0.0   
2                       0.000000    0.0  0.0   
3                      10.909091  100.0  0.0   
4                      20.333333   43.0  0.0   

  HOME_PLAYER_BIG_CHANCES_CREATED_season_sum             \
                                        mean   max  min   
0                                   7.000000  28.0  0.0   
1                                   4.666667  14.0  0.0   
2                                   0.000000   0.0  0.0   
3                                   7.636364  42.0  0.0   
4                                  21.333333  47.0  0.0   

  HOME_PLAYER_BIG_CHANCES_MISSED_season_sum             \
                                       mean   max  min   
0                                  0.000000   0.0  0.0   
1                                  1.833333  11.0  0.0   
2                                  0.000000   0.0  0.0   
3                                  3.000000  22.0  0.0   
4                                 23.000000  37.0  3.0   

  HOME_PLAYER_BLOCKED_SHOTS_season_sum             \
                                  mean   max  min   
0                             1.250000   5.0  0.0   
1                            22.166667  47.0  0.0   
2                             0.000000   0.0  0.0   
3                             4.909091  17.0  0.0   
4                             8.666667  21.0  0.0   

  HOME_PLAYER_CLEARANCES_season_sum             \
                               mean   max  min   
0                          2.250000   6.0  0.0   
1                         22.166667  52.0  0.0   
2                          6.000000   7.0  5.0   
3                          5.000000  30.0  0.0   
4                          4.333333   7.0  3.0   

  HOME_PLAYER_CLEARANCE_OFFLINE_season_sum            \
                                      mean  max  min   
0                                      0.0  0.0  0.0   
1                                      0.0  0.0  0.0   
2                                      0.0  0.0  0.0   
3                                      0.0  0.0  0.0   
4                                      0.0  0.0  0.0   

  HOME_PLAYER_DISPOSSESSED_season_sum              \
                                 mean   max   min   
0                           11.000000  26.0   0.0   
1                           33.833333  70.0   0.0   
2                            0.000000   0.0   0.0   
3                           15.272727  42.0   0.0   
4                           50.666667  81.0  12.0   

  HOME_PLAYER_DRIBBLED_ATTEMPTS_season_sum              \


In [19]:
# Aplatir les colonnes multi-niveaux générées par le groupby ou agrégations précédentes
home_agg.columns = ['_'.join(col).strip() for col in home_agg.columns.values]
home_agg = home_agg.rename(columns={'HOME_ID_' : 'HOME_ID', 'HOME_POSITION_' : 'HOME_POSITION'})

home_agg.head(5)

HOME_ID HOME_POSITION  HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean  \
0    12303      attacker                                      2.500000   
1    12303      defender                                     14.500000   
2    12303    goalkeeper                                      0.000000   
3    12303    midfielder                                      8.909091   
4    12304      attacker                                      5.666667   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_max  \
0                                          7.0   
1                                         48.0   
2                                          0.0   
3                                         68.0   
4                                         11.0   

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min  \
0                                          0.0   
1                                          0.0   
2                                          0.0   
3                                          0.0   
4                                          2.0   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_mean  \
0                                    11.250000   
1                                    35.000000   
2                                    13.000000   
3                                    16.545455   
4                                    13.333333   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_max  \
0                                        17.0   
1                                        70.0   
2                                        22.0   
3                                        39.0   
4                                        19.0   

   HOME_PLAYER_ACCURATE_PASSES_season_sum_min  \
0                                         1.0   
1                                         0.0   
2                                         4.0   
3                                         0.0   
4                                         6.0   

   HOME_PLAYER_AERIALS_WON_season_sum_mean  \
0                                 1.750000   
1                                16.000000   
2                                 1.000000   
3                                 7.363636   
4                                21.666667   

   HOME_PLAYER_AERIALS_WON_season_sum_max  \
0                                     7.0   
1                                    31.0   
2                                     1.0   
3                                    31.0   
4                                    31.0   

   HOME_PLAYER_AERIALS_WON_season_sum_min  \
0                                     0.0   
1                                     0.0   
2                                     1.0   
3                                     0.0   
4                                    12.0   

   HOME_PLAYER_ASSISTS_season_sum_mean  HOME_PLAYER_ASSISTS_season_sum_max  \
0                             5.000000                                20.0   
1                             6.666667                                20.0   
2                             0.000000                                 0.0   
3                            10.909091                               100.0   
4                            20.333333                                43.0   

   HOME_PLAYER_ASSISTS_season_sum_min  \
0                                 0.0   
1                                 0.0   
2                                 0.0   
3                                 0.0   
4                                 0.0   

   HOME_PLAYER_BIG_CHANCES_CREATED_season_sum_mean  \
0                                         7.000000   
1                                         4.666667   
2                                         0.000000   
3                                         7.636364   
4                                        21.333333   

   HOME_PLAYER_BIG_CHANCES_CREATED_season_sum_max  \
0                                            28.0   
1                                            14.0   
2                                             

In [20]:
# Aplatir les colonnes multi-niveaux générées par le groupby ou agrégations précédentes
away_agg.columns = ['_'.join(col).strip() for col in away_agg.columns.values]
away_agg = away_agg.rename(columns={'AWAY_ID_' : 'AWAY_ID', 'AWAY_POSITION_' : 'AWAY_POSITION'})

away_agg.head(5)

AWAY_ID AWAY_POSITION  AWAY_PLAYER_ACCURATE_CROSSES_season_sum_mean  \
0    12303      attacker                                         3.000   
1    12303      defender                                         6.000   
2    12303    goalkeeper                                         0.000   
3    12303    midfielder                                        11.125   
4    12304      attacker                                         3.500   

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_max  \
0                                         12.0   
1                                         21.0   
2                                          0.0   
3                                         75.0   
4                                          7.0   

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_min  \
0                                          0.0   
1                                          0.0   
2                                          0.0   
3                                          0.0   
4                                          0.0   

   AWAY_PLAYER_ACCURATE_PASSES_season_sum_mean  \
0                                         9.25   
1                                        24.00   
2                                        11.50   
3                                        22.75   
4                                        19.50   

   AWAY_PLAYER_ACCURATE_PASSES_season_sum_max  \
0                                        22.0   
1                                        45.0   
2                                        20.0   
3                                        45.0   
4                                        25.0   

   AWAY_PLAYER_ACCURATE_PASSES_season_sum_min  \
0                                         4.0   
1                                         0.0   
2                                         3.0   
3                                        12.0   
4                                        14.0   

   AWAY_PLAYER_AERIALS_WON_season_sum_mean  \
0                                    19.75   
1                                    14.50   
2                                     2.50   
3                                     8.25   
4                                    16.50   

   AWAY_PLAYER_AERIALS_WON_season_sum_max  \
0                                    47.0   
1                                    40.0   
2                                     5.0   
3                                    18.0   
4                                    25.0   

   AWAY_PLAYER_AERIALS_WON_season_sum_min  \
0                                     0.0   
1                                     0.0   
2                                     0.0   
3                                     2.0   
4                                     8.0   

   AWAY_PLAYER_ASSISTS_season_sum_mean  AWAY_PLAYER_ASSISTS_season_sum_max  \
0                             0.000000                                 0.0   
1                             3.333333                                20.0   
2                             0.000000                                 0.0   
3                             7.500000                                40.0   
4                            27.500000                                37.0   

   AWAY_PLAYER_ASSISTS_season_sum_min  \
0                                 0.0   
1                                 0.0   
2                                 0.0   
3                                 0.0   
4                                18.0   

   AWAY_PLAYER_BIG_CHANCES_CREATED_season_sum_mean  \
0                                         3.500000   
1                                         2.333333   
2                                         0.000000   
3                                         3.500000   
4                                        38.000000   

   AWAY_PLAYER_BIG_CHANCES_CREATED_season_sum_max  \
0                                            14.0   
1                                            14.0   
2                                             

In [21]:
# Générer une nouvelle liste de colonnes avec les suffixes pour 'mean', 'min', 'max', 'median'
columns_to_aggregate_home_expanded = []
columns_to_aggregate_away_expanded = []

# Pour home
for col in columns_to_aggregate_home:
    columns_to_aggregate_home_expanded.extend([
        f"{col}_mean", 
        f"{col}_min", 
        f"{col}_max"
        #f"{col}_median"
    ])

# Pour away
for col in columns_to_aggregate_away:
    columns_to_aggregate_away_expanded.extend([
        f"{col}_mean", 
        f"{col}_min", 
        f"{col}_max" 
        #f"{col}_median"
    ])

In [22]:
# Pivot pour home_agg
home_pivot = home_agg.pivot(index='HOME_ID', columns='HOME_POSITION', values=columns_to_aggregate_home_expanded)

home_pivot.head(5)

HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean             \
HOME_POSITION                                     attacker   defender   
HOME_ID                                                                 
12303                                             2.500000  14.500000   
12304                                             5.666667  10.500000   
12305                                             0.250000   1.250000   
12306                                                  NaN   4.500000   
12307                                            10.250000  17.428571   

                                     \
HOME_POSITION goalkeeper midfielder   
HOME_ID                               
12303                0.0   8.909091   
12304                0.0   4.625000   
12305                0.0  21.125000   
12306                0.0   9.400000   
12307                0.0   2.400000   

              HOME_PLAYER_ACCURATE_CROSSES_season_sum_min                      \
HOME_POSITION                                    attacker defender goalkeeper   
HOME_ID                                                                         
12303                                                 0.0      0.0        0.0   
12304                                                 2.0      2.0        0.0   
12305                                                 0.0      0.0        0.0   
12306                                                 NaN      0.0        0.0   
12307                                                 0.0      0.0        0.0   

                         HOME_PLAYER_ACCURATE_CROSSES_season_sum_max           \
HOME_POSITION midfielder                                    attacker defender   
HOME_ID                                                                         
12303                0.0                                         7.0     48.0   
12304                0.0                                        11.0     43.0   
12305                0.0                                         1.0      3.0   
12306                0.0                                         NaN     18.0   
12307                0.0                                        37.0     54.0   

                                     \
HOME_POSITION goalkeeper midfielder   
HOME_ID                               
12303                0.0       68.0   
12304                0.0       16.0   
12305                0.0      100.0   
12306                0.0       43.0   
12307                0.0        6.0   

              HOME_PLAYER_ACCURATE_PASSES_season_sum_mean             \
HOME_POSITION                                    attacker   defender   
HOME_ID                                                                
12303                                           11.250000  35.000000   
12304                                           13.333333  30.333333   
12305                                            9.500000  47.250000   
12306                                                 NaN  26.166667   
12307                                            8.250000  19.571429   

                                     \
HOME_POSITION goalkeeper midfielder   
HOME_ID                               
12303               13.0  16.545455   
12304               14.0  11.500000   
12305               14.5  28.625000   
12306                9.5  29.300000   
12307                6.0  20.600000   

              HOME_PLAYER_ACCURATE_PASSES_season_sum_min                      \
HOME_POSITION                                   attacker defender goalkeeper   
HOME_ID                                                                        
12303                                                1.0      0.0        4.0   
12304                                                6.0      4.0        0.0   
12305                                                2.0     40.0        0.0   
12306                                                NaN      7.0        1.0   
12307                                                0.

In [23]:
# Aplatir les colonnes multi-niveaux générées par pivot_table
home_pivot.columns = ['_'.join(col).strip() for col in home_pivot.columns.values]
home_pivot.reset_index(inplace=True)

home_pivot.head(5)

HOME_ID  HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean_attacker  \
0    12303                                           2.500000       
1    12304                                           5.666667       
2    12305                                           0.250000       
3    12306                                                NaN       
4    12307                                          10.250000       

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean_defender  \
0                                          14.500000       
1                                          10.500000       
2                                           1.250000       
3                                           4.500000       
4                                          17.428571       

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean_goalkeeper  \
0                                                0.0         
1                                                0.0         
2                                                0.0         
3                                                0.0         
4                                                0.0         

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean_midfielder  \
0                                           8.909091         
1                                           4.625000         
2                                          21.125000         
3                                           9.400000         
4                                           2.400000         

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min_attacker  \
0                                                0.0      
1                                                2.0      
2                                                0.0      
3                                                NaN      
4                                                0.0      

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min_defender  \
0                                                0.0      
1                                                2.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min_goalkeeper  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                                                0.0        

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min_midfielder  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                                                0.0        

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_max_attacker  \
0                                                7.0      
1                                               11.0      
2                                                1.0      
3                                                NaN      
4                                               37.0      

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_max_defender  \
0                                               48.0      
1                                               43.0      
2                                                3.0      
3                                               18.0      
4                                               54.0      

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_max_goalkeeper  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                     

In [24]:
# Pivot pour away_agg
away_pivot = away_agg.pivot(index='AWAY_ID', columns='AWAY_POSITION', values=columns_to_aggregate_away_expanded)

# Aplatir les colonnes multi-niveaux générées par pivot_table
away_pivot.columns = ['_'.join(col).strip() for col in away_pivot.columns.values]
away_pivot.reset_index(inplace=True)

away_pivot.head(5)

AWAY_ID  AWAY_PLAYER_ACCURATE_CROSSES_season_sum_mean_attacker  \
0    12303                                           3.000000       
1    12304                                           3.500000       
2    12305                                           0.333333       
3    12306                                                NaN       
4    12307                                           3.000000       

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_mean_defender  \
0                                               6.00       
1                                               0.75       
2                                              11.00       
3                                               5.00       
4                                               9.80       

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_mean_goalkeeper  \
0                                                0.0         
1                                                0.0         
2                                                0.0         
3                                                0.0         
4                                                0.0         

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_mean_midfielder  \
0                                          11.125000         
1                                           7.700000         
2                                           4.428571         
3                                          15.100000         
4                                          16.000000         

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_min_attacker  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                NaN      
4                                                0.0      

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_min_defender  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_min_goalkeeper  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                                                0.0        

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_min_midfielder  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                                                0.0        

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_max_attacker  \
0                                               12.0      
1                                                7.0      
2                                                1.0      
3                                                NaN      
4                                                8.0      

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_max_defender  \
0                                               21.0      
1                                                1.0      
2                                               45.0      
3                                               11.0      
4                                               29.0      

   AWAY_PLAYER_ACCURATE_CROSSES_season_sum_max_goalkeeper  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                     

In [25]:
# Je fais maintenant le merge sur l'ID des matchs. 

home_pivot.rename(columns={'HOME_ID': 'ID'}, inplace=True)
away_pivot.rename(columns={'AWAY_ID': 'ID'}, inplace=True)

sub_data_players = home_pivot.merge(away_pivot, on='ID', how='inner')

sub_data_players.head(5)

ID  HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean_attacker  \
0  12303                                           2.500000       
1  12304                                           5.666667       
2  12305                                           0.250000       
3  12306                                                NaN       
4  12307                                          10.250000       

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean_defender  \
0                                          14.500000       
1                                          10.500000       
2                                           1.250000       
3                                           4.500000       
4                                          17.428571       

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean_goalkeeper  \
0                                                0.0         
1                                                0.0         
2                                                0.0         
3                                                0.0         
4                                                0.0         

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_mean_midfielder  \
0                                           8.909091         
1                                           4.625000         
2                                          21.125000         
3                                           9.400000         
4                                           2.400000         

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min_attacker  \
0                                                0.0      
1                                                2.0      
2                                                0.0      
3                                                NaN      
4                                                0.0      

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min_defender  \
0                                                0.0      
1                                                2.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min_goalkeeper  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                                                0.0        

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_min_midfielder  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                                                0.0        

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_max_attacker  \
0                                                7.0      
1                                               11.0      
2                                                1.0      
3                                                NaN      
4                                               37.0      

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_max_defender  \
0                                               48.0      
1                                               43.0      
2                                                3.0      
3                                               18.0      
4                                               54.0      

   HOME_PLAYER_ACCURATE_CROSSES_season_sum_max_goalkeeper  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                                    

In [26]:
train_data_players = pd.read_csv('../data/Train_Data/players_df.csv')

missing_columns_1 = find_missing_columns_bidirectional(train_data_players, sub_data_players)

# print("Colonnes présentes dans 1 mais manquantes dans 2 :", missing_columns['missing_in_df2'])
# print("Colonnes présentes dans 2 mais manquantes dans 1 :", missing_columns['missing_in_df1'])

sub_data_players = sub_data_players.drop(columns=missing_columns_1['missing_in_df1'])

missing_columns_home_2 = find_missing_columns_bidirectional(train_data_players, sub_data_players)

print("Colonnes présentes dans 2 mais manquantes dans 1 :", missing_columns_home_2['missing_in_df1'])

Colonnes présentes dans 2 mais manquantes dans 1 : []


In [27]:
spot_columns(sub_data_players, percent=10)

In [28]:
# On va tout input avec les médianes comme il n'y a pas de colonnes où il manque
# plus de 10% de NaNs. 

for col in sub_data_players.columns[sub_data_players.isna().mean() < 1]:
    sub_data_players.fillna({col: sub_data_players[col].median()}, inplace=True)

spot_columns(sub_data_players, percent=0)

In [29]:
sub_data_players.shape

(25368, 1585)

In [30]:
# Fusionner avec les données des équipes.
sub_data = sub_data_teams.merge(sub_data_players, on='ID', how='left')

sub_data = sub_data.set_index('ID')

sub_data.head(5)

HOME_TEAM_SHOTS_TOTAL_season_sum  HOME_TEAM_SHOTS_INSIDEBOX_season_sum  \
ID                                                                              
12303                               3.0                                   6.0   
12304                               3.0                                   2.0   
12305                               7.0                                  10.0   
12306                               5.0                                   7.0   
12307                               5.0                                   4.0   

       HOME_TEAM_SHOTS_OFF_TARGET_season_sum  \
ID                                             
12303                                    5.0   
12304                                    4.0   
12305                                    8.0   
12306                                    5.0   
12307                                    6.0   

       HOME_TEAM_SHOTS_ON_TARGET_season_sum  \
ID                                            
12303                                   1.0   
12304                                   2.0   
12305                                   8.0   
12306                                   9.0   
12307                                   3.0   

       HOME_TEAM_SHOTS_OUTSIDEBOX_season_sum  HOME_TEAM_PASSES_season_sum  \
ID                                                                          
12303                                    3.0                          9.0   
12304                                    6.0                          1.0   
12305                                    1.0                          4.0   
12306                                    5.0                          7.0   
12307                                    5.0                          0.0   

       HOME_TEAM_SUCCESSFUL_PASSES_season_sum  HOME_TEAM_SAVES_season_sum  \
ID                                                                          
12303                                     8.0                        10.0   
12304                                     1.0                         2.0   
12305                                     5.0                         0.0   
12306                                     6.0                         3.0   
12307                                     0.0                         2.0   

       HOME_TEAM_CORNERS_season_sum  HOME_TEAM_FOULS_season_sum  \
ID                                                                
12303                           6.0                         7.0   
12304                           4.0                        10.0   
12305                          10.0                         4.0   
12306                           5.0                         8.0   
12307                           2.0                         9.0   

       HOME_TEAM_YELLOWCARDS_season_sum  HOME_TEAM_REDCARDS_season_sum  \
ID                                                                       
12303                               6.0                            3.0   
12304                               7.0                           10.0   
12305                               2.0                            2.0   
12306                               6.0                            8.0   
12307                              10.0                           10.0   

       HOME_TEAM_OFFSIDES_season_sum  HOME_TEAM_ATTACKS_season_sum  \
ID                                                                   
12303                            2.0                           7.0   
12304                            3.0                           2.0   
12305                            0.0                           6.0   
12306                            6.0                           2.0   
12307                            5.0                           8.0   

       HOME_TEAM_PENALTIES_season_sum  HOME_TEAM_SUBSTITUTIONS_season_sum  \
ID                                                                          
12303                             2.0                     

In [31]:
# Exportation du fichier final

sub_data.to_csv('../data/Sub_Data/7_sub_data.csv')